# Program `GEMTB`
## Programmed by Tokuro Fukui

In [ ]:
#--------
# Module
#--------
import numpy as np
import mpmath as mp
import scipy as sp
from scipy.linalg import eig, eigh
from scipy import integrate
from scipy.special import roots_legendre
from scipy.interpolate import CubicSpline
from scipy.special import spherical_jn
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import rcParams

## Disable output scrolling
from IPython.display import display, HTML
display(HTML("<style>.scroll_box { height:200%  !important; }</style>"))

In [ ]:
#-----------------
# Input variables
#-----------------
## Physical constants
pi = np.pi
hc = 197.3269601               # \hbar c (MeV fm)
m_p = 938.2720                 # Proton mass (MeV)
m_n = 939.5654                 # Neutron mass (MeV)
muac = m_p * m_n / (m_p + m_n) # Reduce mass (MeV)

## GEM parameters
nbmx = 20  # Number of Gaussian basis functions
bmn = 0.5  # Minimum value of Gaussian range (fm)
bmx = 20.0 # Maximum value of Gaussian range (fm)
rho = (bmx / bmn)**(1 / (nbmx - 1))
idxmx = nbmx * 2

## Wave-function output and Fourier transform (coordinate space)
rmx = 30.0 # Maximum value of output (fm)
dr = 0.1   # Increments of output (fm)
irmx = int(rmx / dr) + 1

## Wave-function output (momentum space)
kmx = 5.0 # Maximum value of output (fm^{-1})
dk = 0.02   # Increments of output (fm^{-1})
ikmx = int(kmx / dk) + 1

In [ ]:
#-----------------------------------
# Radial function of G3RS potential
#-----------------------------------
def g3rs(r, v0, r0):
    vg3rs = 0.0
    for i in range(3):
        vg3rs += v0[i] * np.exp(-(r / r0[i])**2)
    return vg3rs
    
#----------------
# Plot G3RS 3E-1
#----------------
vc = np.array([-5.0, -230.0, 2000.0])
rc = np.array([2.5, 0.942, 0.447])
vt = np.array([-7.5, -67.5, 67.5])
rt = np.array([2.5, 1.2, 0.447])
vpot = np.zeros((irmx, 2))

for ir in range(irmx):
    r = ir * dr
    c =  g3rs(r, vc, rc) # Central
    t =  g3rs(r, vt, rt) # Tensor
    vpot[ir, 0] = c
    vpot[ir, 1] = t    
    
r_set = np.linspace(0, rmx, irmx)
plt.figure(figsize=(16, 4.5))
plt.subplot(1, 2, 1)
plt.xlim([0.0, 3.0])
plt.ylim([-100, 2000])
plt.axhline(y=0, color="black", linestyle="--", linewidth=1)
plt.plot(r_set, vpot[:, 0], linewidth=3, label="Central")
plt.plot(r_set, vpot[:, 1], linewidth=3, label="Tensor")
plt.title("G3RS 3E-1 potentials")
plt.xlabel("r (fm)")
plt.ylabel("$v(r)$ (MeV)")
plt.tick_params(axis='both', direction='in')
plt.legend()
plt.subplots_adjust(wspace=0.3)

plt.subplot(1, 2, 2)
plt.xlim([0.0, 3.0])
plt.ylim([-100, 100])
plt.axhline(y=0, color="black", linestyle="--", linewidth=1)
plt.plot(r_set, vpot[:, 0], linewidth=3, label="Central")
plt.plot(r_set, vpot[:, 1], linewidth=3, label="Tensor")
plt.title("G3RS 3E-1 potentials")
plt.xlabel("r (fm)")
plt.ylabel("$v(r)$ (MeV)")
plt.tick_params(axis='both', direction='in')
plt.legend()

plt.show()

# Tips for exercise
- テンソル力による$S$-$D$混合を取り入れて重陽子を解こう
- 非対角成分の2体行列要素がゼロになっている
    - 以下のセルで修正すべき行は、現在コメントアウトしてあり、`### Exercise!`と記してある
- `wt1`および`V02[i, j]`に必要な`Vij`を計算しよう
    - `wt1`は資料の式(B.35), $W_{ij}^{(\mathrm{T1})} = \frac{3\sqrt{\pi}}{8} \sum_{k=1}^3 v_k^{(\mathrm{T})} \left(\nu_i+\nu_j+\nu_k^{(\mathrm{T})}\right)^{-5/2}$に対応している
    - `V02[i, j]`は資料の式(B.27)右辺における非対角成分、$2\sqrt{2}N_i^{(0)} N_j^{(2)} W_{ij}^{(\mathrm{T1})}$である
- $N_i^{(l)}$は`Nfac`である。したがって、$N_i^{(l)}$と$N_j^{(l')}$は`Nfac[idx]`と`Nfac[jdx]`として使用すればよい


In [ ]:
#-----------------
# Matrix elements
#-----------------
## Arrays
nu = np.zeros(idxmx)           # Range parameter
Nfac = np.zeros(idxmx)         # Normalization factor
Nij = np.zeros((idxmx, idxmx)) # Norm-matrix elements
Hij = np.zeros((idxmx, idxmx)) # Hamiltonian-matrix elements
V00 = np.zeros((nbmx, nbmx))   # For visualization
V02 = np.zeros((nbmx, nbmx))   # For visualization
V22 = np.zeros((nbmx, nbmx))   # For visualization

## Range parameter and normalization factor
for idx in range(idxmx):
    l = int(idx / nbmx) * 2
    i = int(idx - nbmx * l / 2)

    b = bmn * rho**i
    nu[idx] = 1.0 / b**2
    Nfac[idx] = np.sqrt(2.0**(l + 2) / mp.fac2(2 * l + 1)) * ((2.0 * nu[idx])**(2 * l + 3) / pi)**(0.25)

## Calculation of matrix elements
for idx in range(idxmx):
    li = int(idx / nbmx) * 2
    i = int(idx - nbmx * li / 2)

    for jdx in range(idx + 1):
        lj = int(jdx / nbmx) * 2
        j = int(jdx - nbmx * lj / 2)

        beta = 2.0 * np.sqrt(nu[idx] * nu[jdx]) / (nu[idx] + nu[jdx])
        Nij[idx, jdx] = beta**(li + 1.5) if li == lj else 0
        Nij[jdx, idx] = Nij[idx, jdx]

        coeff_T = hc**2 / muac * (2.0 * li + 3.0) * nu[idx] * nu[jdx] / (nu[idx] + nu[jdx])
        Tij = coeff_T * Nij[idx, jdx]

        wc1  = 0.0
        wc2  = 0.0
        wt1 = 0.0
        wt2 = 0.0
        for k in range(3):
            nuc = 1.0 / rc[k]**2
            nut = 1.0 / rt[k]**2
            wc1 += vc[k] * (nu[idx] + nu[jdx] + nuc)**(-1.5)
            wc2 += vc[k] * (nu[idx] + nu[jdx] + nuc)**(-3.5)
            # wt1 *= ### Exercise! See Eq. (B.35) ###
            wt2 += vt[k] * (nu[idx] + nu[jdx] + nut)**(-3.5)

        wc1 *= np.sqrt(pi) * 0.25   # 1/4
        wc2 *= np.sqrt(pi) * 0.9375 # 15/16
        # wt1 += ### Exercise! See Eq. (B.35) ###
        wt2 *= np.sqrt(pi) * 0.9375 # 15/16

        if li == lj and li == 0:
            Vij = Nfac[idx] * Nfac[jdx] * wc1
            V00[i, j] = Vij
        elif li == lj and li == 2:
            Vij = Nfac[idx] * Nfac[jdx] * (wc2 - 2.0 * wt2)
            V22[i, j] = Vij
        else:
            Vij = 0.0 ### Exercise! Remove this value and give correct equation below.
            # Vij = ### Exercise! See Eq. (B.27) ###
            V02[i, j] = Vij

        Hij[idx, jdx] = Tij + Vij
        Hij[jdx, idx] = Hij[idx, jdx]
        V00[j, i] = V00[i, j]
        V22[j, i] = V22[i, j]
        V02[j, i] = V02[i, j]

## Visualization of matrix elements
b_series = [bmn * rho**i for i in range(nbmx)]
bi, bj = np.meshgrid(b_series, b_series)

fig = plt.figure()
ax = fig.add_subplot(111, projection="3d")
surf = ax.plot_surface(bi, bj, V00, cmap="viridis", alpha=0.6)
ax.set_xlabel("$b_i$ (fm)")
ax.set_ylabel("$b_j$ (fm)")
ax.zaxis.set_rotate_label(False)
ax.text(0.5, 22.5, 1200.0, "$V_{ij}^{(00)}$ (MeV)", rotation=0, ha='center', va='center', fontsize=12)
ax.set_xticks(np.arange(0.0, 21.0, 5.0))
ax.set_yticks(np.arange(0.0, 21.0, 5.0))
ax.set_zticks(np.arange(0.0, 1001.0, 250))
rcParams['axes.labelpad'] = 3
ax.set_title("$^3S_1$")
ax.view_init(elev=25, azim=230)
fig.colorbar(surf, ax=ax, shrink=0.5, aspect=5)
surf.set_clim(0.0, 1000.0)
plt.show()

fig = plt.figure()
ax = fig.add_subplot(111, projection="3d")
surf = ax.plot_surface(bi, bj, V22, cmap="viridis", alpha=0.6)
ax.set_xlabel("$b_i$ (fm)")
ax.set_ylabel("$b_j$ (fm)")
ax.zaxis.set_rotate_label(False)
ax.text(0.5, 22.5, 600, "$V_{ij}^{(22)}$ (MeV)", rotation=0, ha='center', va='center', fontsize=12)
ax.set_xticks(np.arange(0.0, 21.0, 5.0))
ax.set_yticks(np.arange(0.0, 21.0, 5.0))
ax.set_zticks(np.arange(0.0, 501.0, 100))
rcParams['axes.labelpad'] = 3
ax.set_title("$^3D_1$")
ax.view_init(elev=25, azim=230)
fig.colorbar(surf, ax=ax, shrink=0.5, aspect=5)
surf.set_clim(0.0, 500.0)
plt.show()

fig = plt.figure()
ax = fig.add_subplot(111, projection="3d")
surf = ax.plot_surface(bi, bj, V02, cmap="viridis", alpha=0.6)
ax.set_xlabel("$b_i$ (fm)")
ax.set_ylabel("$b_j$ (fm)")
ax.zaxis.set_rotate_label(False)
ax.text(0.5, 22.5, 15.0, "$V_{ij}^{(02)}$ (MeV)", rotation=0, ha='center', va='center', fontsize=12)
ax.set_xticks(np.arange(0.0, 21.0, 5.0))
ax.set_yticks(np.arange(0.0, 21.0, 5.0))
ax.set_zticks(np.arange(-100.0, 0.1, 20.0))
rcParams['axes.labelpad'] = 3
ax.set_title("$^3S_1$-$^3D_1$")
ax.view_init(elev=25, azim=230)
fig.colorbar(surf, ax=ax, shrink=0.5, aspect=5)
surf.set_clim(None, 0.0)
plt.show()

In [ ]:
#------------------------------------------
# Check for generalized eigenvalue problem
#------------------------------------------
def eig_check(A, B, eigval, eigvec):
    return np.linalg.norm(A.dot(eigvec) - eigval * B.dot(eigvec))

def eig_checks(A, B, eigval, eigvec):
    r = np.zeros(eigval.shape[0])
    i = 0
    for e, v in zip(eigval, eigvec.T):
        r[i] = eig_check(A, B, e, v)
        i += 1
    return r

In [ ]:
#--------------------------------
# Generalized eigenvalue problem
#--------------------------------
## Diagonalization
eval, evec = eigh(Hij, Nij)
print("Ground-state energy\n", eval[0], "(MeV)")
# print('\nEivenvector: \n', evec[0])

## Check for generalized eigenvalue problem
def eig_check(A, B, eigval, eigvec):
    return np.linalg.norm(A.dot(eigvec) - eigval * B.dot(eigvec))

def eig_checks(A, B, eigval, eigvec):
    r = np.zeros(eigval.shape[0])
    i = 0
    for e, v in zip(eigval, eigvec.T):
        r[i] = eig_check(A, B, e, v)
        i += 1
    return r

print("\nCheck for generalized eigenvalue problem\n", eig_checks(Hij, Nij, eval, evec))

## Normalization
Anorm = np.zeros(2)
l_num = -1
for l in range(0, 3, 2): 
    l_num += 1
    for i in range(nbmx):
        for j in range(nbmx):
            idx = int(i + nbmx * l / 2)
            jdx = int(j + nbmx * l / 2)
            Anorm[l_num] += evec[idx, 0] * evec[jdx, 0] * Nij[idx, jdx]

Anorm[:] = 1.0 / np.sqrt(Anorm[:])
spro = 1.0 / Anorm[0]**2
dpro = 1.0 / Anorm[1]**2
print("\nProbability", "\n P(S) = ", spro, "\n P(D) = ", dpro, "\n P(S) + P(D) = ", spro + dpro)

## Wave function in coordinate space
wf = np.zeros((irmx, 2))
for ir in range(irmx):
    r = ir * dr

    for idx in range(idxmx):
        l = int(idx / nbmx) * 2
        i = int(idx - nbmx * l / 2)
        l_num = int(l / 2)

        phi = r**(l + 1) * np.exp(-nu[idx] * r**2)
        wf[ir, l_num] += evec[idx, 0] * Nfac[idx] * phi

## Wave function in momentum space
wfmom = np.zeros((ikmx, 2))
sumk0 = 0.0
for ik in range(ikmx):
    k = ik * dk

    for idx in range(idxmx):
        l = int(idx / nbmx) * 2
        i = int(idx - nbmx * l / 2)
        l_num = int(l / 2)

        phimom = k**(l + 1) * np.exp(-0.25 * k**2 / nu[idx])
        wfmom[ik, l_num] += 1.0 / (2.0 * nu[idx])**(l + 1.5) * evec[idx, 0] * Nfac[idx] * phimom

print()
k_set = np.linspace(0, kmx, ikmx)
plt.figure(figsize=(16, 4.5))
plt.subplot(1, 2, 1)
plt.xlim([0.0, 20.0])
plt.ylim([0.0, 0.6])
plt.plot(r_set, -wf[:, 0], label="S ($l=0$)")
plt.plot(r_set, -wf[:, 1], label="D ($l=2$)")
plt.xlabel("$r$ (fm)")
plt.ylabel("$u_{l}(r)$ (fm$^{-1/2}$)")
plt.tick_params(axis='both', direction='in')
plt.title("Wave function in coordinate space\n G3RS 3E-1")
plt.legend()
plt.subplots_adjust(wspace=0.3)

plt.subplot(1, 2, 2)
plt.xlim([0.0, kmx])
plt.axhline(y=0, color="black", linestyle="--", linewidth=1)
plt.plot(k_set, -wfmom[:, 0], label="S ($l=0$)")
plt.plot(k_set, -wfmom[:, 1], label="D ($l=2$)")
plt.xlabel("$k$ (fm$^{-1}$)")
plt.ylabel("$\\tilde u_{l}(k)$ (fm$^{1/2}$)")
plt.tick_params(axis='both', direction='in')
plt.title("Wave function in momentum space\n G3RS 3E-1")
plt.legend()

plt.show()

# History
## Ver. 00a00 (9/July/2024)
1. First version released.
1. Deuteon (S-wave only) was assumed with a central Yukawa potential.

## Ver. 00a01 (9/July/2024)
1. A bug related to the preparation of the Gaussian range parameters was fixed.

## Ver. 00a02 (15/July/2024)
1. Computation of the matrix elements is now more efficient owing to their symmetry.

## Ver. 00b00 (16/July/2024)
1. S-D coupling cased by the tensor interaction was implemented using the G3RS potential.

## Ver. 00b01 (16/July/2024)
1. A bug related to the normalization was fixed.

## Ver. 00b02 (18/July/2024)
1. Two-body matrix elements are now visualized.
2. An error on the formalism of the two-body matrix elements was fixed.

## Ver. 00b03 (23/July/2024)
1. The quadrupole moment was computed.
2. An error on the wave-function output was fixed.

## Ver. 00b04 (18/October/2024)
1. The momemtum distribution was computed.

## Ver. 00b05 (25/February/2025)
1. The structure of the code was slightly modified.